# IRC Bots

Making bots as a way to re(turn) to gamification mechanisms and find ways to subvert them.

Possible links to start in the middle of:

* https://pad.xpub.nl/p/18012022 - Pad of the session on "Defining play and games, Blurrying the lines between labour and play: gamification and playbour" 
* https://pad.xpub.nl/p/2022_onesentencegameideas


## How to make an IRC bot?

* **example script**: https://pzwiki.wdka.nl/mediadesign/Building_an_IRC_bot_in_python
* **IRC server** for this notebooks: https://libera.chat/
* **Python library**: irc

## Where to interact with the bots?

* **IRC web client**: https://web.libera.chat
* **channel**: #xpub

In [1]:
! pip3 install irc

Defaulting to user installation because normal site-packages is not writeable
Looking in indexes: https://pypi.org/simple, https://www.piwheels.org/simple
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


In [2]:
! /usr/bin/python3 -m pip install --upgrade pip

Defaulting to user installation because normal site-packages is not writeable
Looking in indexes: https://pypi.org/simple, https://www.piwheels.org/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 6.4 MB/s eta 0:00:00:00:0100:01
  Attempting uninstall: pip
    Found existing installation: pip 22.0.3
    Uninstalling pip-22.0.3:
      Successfully uninstalled pip-22.0.3
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.


## Python's "class"

The irc library works with a Python element that we have not worked with yet, called a **class**. Classes are program-code-templates that are extensible.

> Classes provide a means of bundling data and functionality together. Creating a new class creates a new type of object, allowing new instances of that type to be made. Each class instance can have attributes attached to it for maintaining its state. Class instances can also have methods (defined by its class) for modifying its state.

https://docs.python.org/3/tutorial/classes.html

If you want to learn more about classes, you can start here: http://introtopython.org/classes.html#What-are-classes?

## hellobot

In [1]:
import irc.bot



class HelloBot(irc.bot.SingleServerIRCBot):
    def __init__(self, channel, nickname, server, port):
        irc.bot.SingleServerIRCBot.__init__(self, [(server, port)], nickname, nickname)
        self.channel = channel

    def on_welcome(self, connection, event):
        connection.join(self.channel)

    def on_privmsg(self, connection, event):
        pass

    def on_pubmsg(self, connection, event):
        # event.target, event.source, event.arguments, event.type
        # print(event) 
        # type: pubmsg, source: Guest92843793284!~Guest9284@2a10:3781:1734:1:fdd8:ab9a:d925:9106, target: #xpub, arguments: ['...'], tags: []
        messages = event.arguments # list of messages
        for message in messages:
            if "hello" in message:
                connection.privmsg(self.channel, "HELLO!!!")
            if "bye" in message:
                connection.privmsg(self.channel, "BYE!!!")

server = "irc.libera.chat"
port = 6667
channel = "#xpub"
nickname = "hellobot"

bot = HelloBot(channel, nickname, server, port)
bot.start()

KeyboardInterrupt: 

## echobot

In [ ]:
import irc.bot

class EchoBot(irc.bot.SingleServerIRCBot):
    def __init__(self, channel, nickname, server, port):
        irc.bot.SingleServerIRCBot.__init__(self, [(server, port)], nickname, nickname)
        self.channel = channel

    def on_welcome(self, connection, event):
        connection.join(self.channel)

    def on_privmsg(self, connection, event):
        pass

    def on_pubmsg(self, connection, event):
        # event.target, event.source, event.arguments, event.type
        # print(event) # type: pubmsg, source: Guest92843793284!~Guest9284@2a10:3781:1734:1:fdd8:ab9a:d925:9106, target: #xpub, arguments: ['...'], tags: []
        messages = event.arguments
        for message in messages:
            connection.privmsg(self.channel, message)

server = "irc.libera.chat"
port = 6667
channel = "#xpub"
nickname = "echobot"

bot = EchoBot(channel, nickname, server, port)
bot.start()

## timerbot

In [ ]:
import irc.bot
import time 

class TimerBot(irc.bot.SingleServerIRCBot):
    def __init__(self, channel, nickname, server, port):
        irc.bot.SingleServerIRCBot.__init__(self, [(server, port)], nickname, nickname)
        self.channel = channel
        
        # This is where the last_timer is initiated
        self.last_timer = time.time()

    def on_welcome(self, connection, event):
        connection.join(self.channel)

    def on_privmsg(self, connection, event):
        pass

    def on_pubmsg(self, connection, event):
        # event.target, event.source, event.arguments, event.type
        # print(event) # type: pubmsg, source: Guest92843793284!~Guest9284@2a10:3781:1734:1:fdd8:ab9a:d925:9106, target: #xpub, arguments: ['...'], tags: []
        
        # Make a new timestamp 
        now = time.time()
        
        # Compare "now" with the last_timer
        timer = round((now - self.last_timer), 2)
        
        reply = f"{ timer } seconds"
        connection.privmsg(self.channel, reply)
        
        # Reset the last_timer
        self.last_timer = now

server = "irc.libera.chat"
port = 6667
channel = "#xpub"
nickname = "timerbot"

bot = TimerBot(channel, nickname, server, port)
bot.start()

## bot-with-memory

In [ ]:
import irc.bot
import time 
import os
import json

class CountingBot(irc.bot.SingleServerIRCBot):
    def __init__(self, channel, nickname, server, port):
        irc.bot.SingleServerIRCBot.__init__(self, [(server, port)], nickname, nickname)
        self.channel = channel
        
        # --- database settings ---
        self.db_filename = 'countingbot.json'
        self.db = self.load_db()
        # -------------------------
 
    # --- database functions ---
    def write_db(self, this_db):
        with open(self.db_filename, 'w+') as f:
            f.write(json.dumps(this_db, indent=4, sort_keys=True))

    def load_db(self):
        # Create the database when it does not exist yet
        if not os.path.exists(self.db_filename):
            new_db = {}
            self.write_db(new_db)
        with open(self.db_filename, 'r') as f:
            db = json.loads(f.read())

        return db

    def read_db(self, key):
        if key in self.db:
            return self.db[key]
        else:
            return None

    def update_db(self, key, value):
        self.db[key] = value
        self.write_db(self.db)
    # -------------------------

    def on_welcome(self, connection, event):
        connection.join(self.channel)

    def on_privmsg(self, connection, event):
        pass

    def on_pubmsg(self, connection, event):
        # event.target, event.source, event.arguments, event.type
        # print(event) # type: pubmsg, source: Guest92843793284!~Guest9284@2a10:3781:1734:1:fdd8:ab9a:d925:9106, target: #xpub, arguments: ['...'], tags: []
        
        # First check if there is a counter already,
        # and if not, make one
        if self.read_db("count") == None:
            current_count = self.update_db("count", 0)
        
        current_count = self.read_db("count")            
        new_count = current_count + 1
        self.update_db("count", new_count)
        reply = str(new_count)
        
        connection.privmsg(self.channel, reply)

server = "irc.libera.chat"
port = 6667
channel = "#xpub"
nickname = "countingbot"

bot = CountingBot(channel, nickname, server, port)
bot.start()